<a href="https://colab.research.google.com/github/yuanjinren/DS-Unit-2-Applied-Modeling/blob/master/module1-define-ml-problems/YuanjinRen_LS_DS_231_assignment.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Lambda School Data Science

*Unit 2, Sprint 3, Module 1*

---


# Define ML problems

You will use your portfolio project dataset for all assignments this sprint.

## Assignment

Complete these tasks for your project, and document your decisions.

- [ ] Choose your target. Which column in your tabular dataset will you predict?
- [ ] Is your problem regression or classification?
- [ ] How is your target distributed?
    - Classification: How many classes? Are the classes imbalanced?
    - Regression: Is the target right-skewed? If so, you may want to log transform the target.
- [ ] Choose your evaluation metric(s).
    - Classification: Is your majority class frequency >= 50% and < 70% ? If so, you can just use accuracy if you want. Outside that range, accuracy could be misleading. What evaluation metric will you choose, in addition to or instead of accuracy?
    - Regression: Will you use mean absolute error, root mean squared error, R^2, or other regression metrics?
- [ ] Choose which observations you will use to train, validate, and test your model.
    - Are some observations outliers? Will you exclude them?
    - Will you do a random split or a time-based split?
- [ ] Begin to clean and explore your data.
- [ ] Begin to choose which features, if any, to exclude. Would some features "leak" future information?

If you haven't found a dataset yet, do that today. [Review requirements for your portfolio project](https://lambdaschool.github.io/ds/unit2) and choose your dataset.

Some students worry, ***what if my model isn't “good”?*** Then, [produce a detailed tribute to your wrongness. That is science!](https://twitter.com/nathanwpyle/status/1176860147223867393)



---


Data Source: https://www.kaggle.com/cnic92/200-financial-indicators-of-us-stocks-20142018

"200+ Financial Indicators of US stocks (2014-2018)"
The last column of the dataset represent the class of each stock, where:

*   if the value of a stock increases during next year, then class=1;
*   if the value of a stock decreases during next year, then class=0.

The second-to-last column, PRICE VAR [%], lists the percent price variation of each stock for the next year. For example, 
percent price variation for the year 2016 (meaning from the first trading day on Jan 2016 to the last trading day on Dec 2016).

The columns PRICE VAR [%] and class make possible to use the datasets for both classification and regression tasks.





In [0]:
import pandas as pd
import numpy as np

In [41]:
df_2014 = pd.read_csv('/content/2014_Financial_Data.csv',index_col=0)
df_2015 = pd.read_csv('/content/2015_Financial_Data.csv',index_col=0)
df_2016 = pd.read_csv('/content/2016_Financial_Data.csv',index_col=0)
df_2017 = pd.read_csv('/content/2017_Financial_Data.csv',index_col=0)
df_2018 = pd.read_csv('/content/2018_Financial_Data.csv',index_col=0)
df_2014.shape,df_2015.shape,df_2016.shape,df_2017.shape,df_2018.shape

((3808, 224), (4120, 224), (4797, 224), (4960, 224), (4392, 224))

In [44]:
df_all = pd.concat([df_2014,df_2015,df_2016,df_2017,df_2018], axis=0, sort=False).drop_duplicates()
df_all.shape

(22077, 228)

In [46]:
df_all.tail()

Revenue  Revenue Growth  ...  2018 PRICE VAR [%]  2019 PRICE VAR [%]
YRIV         0.0          0.0000  ...                 NaN          -90.962099
YTEN    556000.0         -0.4110  ...                 NaN          -77.922077
ZKIN  54884381.0          0.2210  ...                 NaN          -17.834400
ZOM          0.0          0.0000  ...                 NaN          -73.520000
ZYME  53019000.0          0.0243  ...                 NaN          209.462222

[5 rows x 228 columns]

In [48]:
df_all.columns

Index(['Revenue', 'Revenue Growth', 'Cost of Revenue', 'Gross Profit',
       'R&D Expenses', 'SG&A Expense', 'Operating Expenses',
       'Operating Income', 'Interest Expense', 'Earnings before Tax',
       ...
       'Debt Growth', 'R&D Expense Growth', 'SG&A Expenses Growth', 'Sector',
       '2015 PRICE VAR [%]', 'Class', '2016 PRICE VAR [%]',
       '2017 PRICE VAR [%]', '2018 PRICE VAR [%]', '2019 PRICE VAR [%]'],
      dtype='object', length=228)

In [47]:
df_all.isnull().sum()

Revenue                1171
Revenue Growth         2088
Cost of Revenue        1771
Gross Profit           1207
R&D Expenses           2138
                      ...  
Class                     0
2016 PRICE VAR [%]    17957
2017 PRICE VAR [%]    17280
2018 PRICE VAR [%]    17117
2019 PRICE VAR [%]    17685
Length: 228, dtype: int64

In [52]:
df_all['Revenue'].isnull().sum()

1171

In [0]:
df_all['Revenue'].fillna(0, inplace=True)

In [80]:
df_all['Revenue'].isnull().sum()

0

In [81]:
df_all.isnull().sum()

Revenue                   0
Revenue Growth         2088
Cost of Revenue        1771
Gross Profit           1207
R&D Expenses           2138
                      ...  
Class                     0
2016 PRICE VAR [%]    17957
2017 PRICE VAR [%]    17280
2018 PRICE VAR [%]    17117
2019 PRICE VAR [%]    17685
Length: 228, dtype: int64

In [86]:
df_all.rename(columns={'2015 PRICE VAR [%]':'2015',
                       '2016 PRICE VAR [%]':'2016',
                       '2017 PRICE VAR [%]':'2017',
                       '2018 PRICE VAR [%]':'2018',
                       '2019 PRICE VAR [%]':'2019'},inplace=True)
df_all.columns


Index(['Revenue', 'Revenue Growth', 'Cost of Revenue', 'Gross Profit',
       'R&D Expenses', 'SG&A Expense', 'Operating Expenses',
       'Operating Income', 'Interest Expense', 'Earnings before Tax',
       ...
       'Debt Growth', 'R&D Expense Growth', 'SG&A Expenses Growth', 'Sector',
       '2015', 'Class', '2016', '2017', '2018', '2019'],
      dtype='object', length=228)

First of all, I am going to use this dataset for classification problem. 'Class' column is the target. 

In [106]:
df_all['Class'].value_counts()

1    12159
0     9918
Name: Class, dtype: int64

In [89]:
df_cf = df_all.drop(['2015','2016','2017','2018','2019'], axis=1)
df_cf.shape

(22077, 223)

In [0]:
df_cf.fillna(0, inplace=True)

In [91]:
df_cf.isnull().sum().sort_values()

Revenue                           0
Enterprise Value                  0
PE ratio                          0
Price to Sales Ratio              0
POCF ratio                        0
                                 ..
priceEarningsRatio                0
priceToFreeCashFlowsRatio         0
priceToOperatingCashFlowsRatio    0
Dividend payments                 0
Class                             0
Length: 223, dtype: int64

In [123]:
# find the baseline
majority_class = df_all['Class'].mode()
majority_class

0    1
dtype: int64

In [0]:
df_all_pred = [majority_class] * len(df_all[target])

In [125]:
from sklearn.metrics import accuracy_score
accuracy_score(df_all['Class'], df_all_pred)

0.5507541785568691

In [0]:
import category_encoders as ce
from sklearn.model_selection import train_test_split
from sklearn.pipeline import make_pipeline
from sklearn.impute import SimpleImputer
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier

In [0]:
train, test = train_test_split(df_cf, train_size=0.80, test_size=0.20,
                               stratify=df_cf['Class'],random_state=42)

In [97]:
train.shape, test.shape

((17661, 223), (4416, 223))

In [0]:
target = 'Class'
features = train.drop(columns=[target]).columns.tolist()
X_train = train[features]
y_train = train[target]
X_test = test[features]
y_test = test[target]

In [108]:
X_train.shape, y_train.shape, X_test.shape, y_test.shape

((17661, 222), (17661,), (4416, 222), (4416,))

###DecisionTreeClassifier

In [113]:
pipeline = make_pipeline(
    ce.ordinal.OrdinalEncoder(),
    SimpleImputer(),
    DecisionTreeClassifier(random_state=42)

)
pipeline.fit(X_train, y_train)

Pipeline(memory=None,
         steps=[('ordinalencoder',
                 OrdinalEncoder(cols=['Sector'], drop_invariant=False,
                                handle_missing='value', handle_unknown='value',
                                mapping=[{'col': 'Sector',
                                          'data_type': dtype('O'),
                                          'mapping': Financial Services         1
Consumer Cyclical          2
Technology                 3
Healthcare                 4
Utilities                  5
Industrials                6
Consumer Defensive         7
Communication Services     8
Energy                     9
Basic Materials           10
Real Es...
                               verbose=0)),
                ('decisiontreeclassifier',
                 DecisionTreeClassifier(ccp_alpha=0.0, class_weight=None,
                                        criterion='gini', max_depth=None,
                                        max_features=None, max_leaf_nodes=Non

In [117]:
print(f'Train accuray:{pipeline.score(X_train, y_train)}')
print(f'Test accuracy:{pipeline.score(X_test, y_test)}')

Train accuray:0.9806919200498273
Test accuracy:0.5627264492753623


In [118]:
import graphviz
from sklearn.tree import export_graphviz

tree = pipeline.named_steps['decisiontreeclassifier']

dot_data = export_graphviz(
    tree,
    out_file=None,
    feature_names=X_train.columns,
    class_names=y_train.unique().astype(str),
    filled=True,
    impurity=False,
    proportion=True
)

graphviz.Source(dot_data)

###RandomForestClassifier

In [119]:
pipeline2 = make_pipeline(
    ce.ordinal.OrdinalEncoder(),
    SimpleImputer(),
    RandomForestClassifier(n_estimators=100, n_jobs=-1, random_state=42)

)
pipeline2.fit(X_train, y_train)

Pipeline(memory=None,
         steps=[('ordinalencoder',
                 OrdinalEncoder(cols=['Sector'], drop_invariant=False,
                                handle_missing='value', handle_unknown='value',
                                mapping=[{'col': 'Sector',
                                          'data_type': dtype('O'),
                                          'mapping': Financial Services         1
Consumer Cyclical          2
Technology                 3
Healthcare                 4
Utilities                  5
Industrials                6
Consumer Defensive         7
Communication Services     8
Energy                     9
Basic Materials           10
Real Es...
                 RandomForestClassifier(bootstrap=True, ccp_alpha=0.0,
                                        class_weight=None, criterion='gini',
                                        max_depth=None, max_features='auto',
                                        max_leaf_nodes=None, max_samples=None,
        

In [121]:
print(f'Training accuracy: {pipeline2.score(X_train, y_train)}')
print(f'Test accuracy:{pipeline2.score(X_test, y_test)}')

Training accuracy: 0.9806919200498273
Test accuracy:0.6175271739130435


###Performance Evaluation

In [0]:
y_test_pred = pipeline2.predict(X_test)

In [127]:
from sklearn.metrics import classification_report
print(classification_report(y_test, y_test_pred))

              precision    recall  f1-score   support

           0       0.59      0.49      0.54      1984
           1       0.63      0.72      0.67      2432

    accuracy                           0.62      4416
   macro avg       0.61      0.61      0.61      4416
weighted avg       0.61      0.62      0.61      4416

